## Exercise 5 problem 2

#### Code to create an interactive map
##### Here the interactive map presents the travel time ratio between public transportation and car (pt/car) to the Helsinki main railway station. The travel times are only considered inside Helsinki city borders.

In [1]:
# Importing necessary modules
import folium
from pyproj import CRS
import geopandas as gpd
import matplotlib.pyplot as plt
from geopandas.tools import geocode
import os
import numpy as np

In [2]:
# Importing traveltimes data
path = r'data/'
fn =  'TravelTimes_to_5975375_RailwayStation.shp'
fp = os.path.join(path, fn)

traveltimes = gpd.read_file(fp)
traveltimes = traveltimes[['pt_r_t', 'car_r_t', 'geometry']]
traveltimes = traveltimes.to_crs(epsg=4326)

In [3]:
# Assigning and dropping nan from traveltimes
traveltimes[traveltimes == -1] = np.nan
traveltimes = traveltimes.dropna()

In [4]:
# New columns to address the ratio between public transportation and car travel times
traveltimes['pt/car'] = round(traveltimes['pt_r_t']/traveltimes['car_r_t'],2)

In [5]:
# Checking the data
traveltimes['pt/car'].describe()

count    13019.000000
mean         1.473612
std          0.337413
min          0.500000
25%          1.240000
50%          1.430000
75%          1.670000
max          3.550000
Name: pt/car, dtype: float64

In [6]:
# Geocoding the railway station address to be used after
stat = geocode('Kaivokatu 1, 00100 Helsinki', provider='nominatim', user_agent='autogis_xx', timeout=4)
stat.head()

geometry  \
0  POINT (24.94135 60.17178)   

                                             address  
0  Helsinki, 1, Kaivokatu, Keskusta, Kluuvi, Etel...

In [7]:
# Importing Helsinki borders
border_fp = "data/Helsinki_borders.shp"
hel = gpd.read_file(border_fp)
hel.head()

GML_ID   NAMEFIN      NAMESWE NATCODE  \
0  27517366  Helsinki  Helsingfors     091   

                                            geometry  
0  POLYGON ((399936.363 6684600.244, 399937.630 6...

In [8]:
# Helsinki borders into a correct crs
hel = hel.to_crs(crs=4326)

In [9]:
# Checking that all crs match
assert hel.crs == traveltimes.crs, "CRS differs between layers!"
assert hel.crs == stat.crs, "CRS differs between layers!"

In [10]:
# Removing grids outside of Helsinki from the traveltimes variable
traveltimes = gpd.overlay(traveltimes, hel, how='intersection')

In [11]:
# Assigning geoid column and removing unnecessary columns
traveltimes['geoid'] = traveltimes.index.astype(str)
traveltimes = traveltimes[['pt/car', 'geoid', 'geometry']]

In [12]:
# Taking the coordinates of our station location (to be used in plotting)
stat = stat['geometry'].bounds[['miny', 'minx']]

In [13]:
# Plotting the interactive map
# Creating a map instance
m = folium.Map(location=[60.22, 24.99],
                zoom_start=11.9, control_scale=True, prefer_canvas=True)

folium.Choropleth(
    geo_data=traveltimes,
    name='Traveltime ratio (pt/car) to Helsinki railway station',
    data=traveltimes,
    columns=['geoid', 'pt/car'],
    key_on='feature.id',
    fill_color='YlOrRd',
    fill_opacity=0.7,
    line_opacity=0.2,
    line_color='white', 
    line_weight=0,
    highlight=False, 
    smooth_factor=1.0,
    #threshold_scale=myscale,
    legend_name= 'Travel times ratio: Public Transportation/Car').add_to(m)

# Adding a marker at the railway station
folium.Marker(
    location=stat,
    popup='Railway station',
    icon=folium.Icon(color='green', icon='ok-sign'),
).add_to(m)

# Convert points to GeoJson to be able to see traveltime of each grid
folium.features.GeoJson(traveltimes,  
                        name='Labels',
                        style_function=lambda x: {'color':'transparent','fillColor':'transparent','weight':0},
                        tooltip=folium.features.GeoJsonTooltip(fields=['pt/car'],
                                                                aliases = ['Travel time PT/Car'],
                                                                labels=True,
                                                                sticky=False
                                                                            )
                       ).add_to(m)

In [14]:
m

In [15]:
# Save html map into docs folder
myfp = r'docs/'
figname ='Traveltime_Ratios_Helsinki_Railwaystation.html'
outfp = os.path.join(myfp, figname)
m.save(outfp)